# scroll down for spark section

In [ ]:
#should imports and starting a session

In [1]:
import findspark


In [2]:
findspark.init()

In [3]:
import pyspark

In [4]:
import pyspark

In [5]:
from pyspark.sql import SparkSession

In [6]:
spark = SparkSession.builder.getOrCreate()

In [7]:
#df = spark.sql("select 'spark' as hello ")

#df.show()

# sklearn linear regression to test first before spark regression

In [8]:
import pandas as pd 
import numpy as np
df = pd.read_csv("yellow_tripdata_2019-01.csv")
df = df.head(1250000)
#df = df.head(1000)

In [9]:
df.head()

VendorID tpep_pickup_datetime tpep_dropoff_datetime  passenger_count  \
0         1  2019-01-01 00:46:40   2019-01-01 00:53:20                1   
1         1  2019-01-01 00:59:47   2019-01-01 01:18:59                1   
2         2  2018-12-21 13:48:30   2018-12-21 13:52:40                3   
3         2  2018-11-28 15:52:25   2018-11-28 15:55:45                5   
4         2  2018-11-28 15:56:57   2018-11-28 15:58:33                5   

   trip_distance  RatecodeID store_and_fwd_flag  PULocationID  DOLocationID  \
0            1.5           1                  N           151           239   
1            2.6           1                  N           239           246   
2            0.0           1                  N           236           236   
3            0.0           1                  N           193           193   
4            0.0           2                  N           193           193   

   payment_type  fare_amount  extra  mta_tax  tip_amount  tolls_amount  \
0             1          7.0    0.5      0.5        1.65           0.0   
1             1         14.0    0.5      0.5        1.00           0.0   
2             1          4.5    0.5      0.5        0.00           0.0   
3             2          3.5    0.5      0.5        0.00           0.0   
4             2         52.0    0.0      0.5        0.00           0.0   

   improvement_surcharge  total_amount  congestion_surcharge  
0                    0.3          9.95                   NaN  
1                    0.3         16.30                   NaN  
2                    0.3          5.80                   NaN  
3                    0.3          7.55                   NaN  
4                    0.3         55.55                   NaN

In [10]:
df = df[df['total_amount']>0]
df = df[df['fare_amount']>0]
df = df[df['total_amount']<300]
df = df[df['fare_amount']<200]

In [11]:
df = df.drop(['tpep_pickup_datetime'], axis=1)
df = df.drop(['tpep_dropoff_datetime'], axis=1)
df = df.drop(['store_and_fwd_flag'], axis=1)

In [12]:
X = df[['VendorID',
       'passenger_count', 'trip_distance', 'RatecodeID', 
       'PULocationID', 'DOLocationID', 'payment_type', 'extra',
       'mta_tax', 'tip_amount', 'tolls_amount', 'improvement_surcharge']]
y = df['fare_amount']

In [13]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)

In [14]:
from sklearn.linear_model import LinearRegression
regressor = LinearRegression()
regressor.fit(X_train, y_train)

LinearRegression()

In [15]:
coeff_df = pd.DataFrame(regressor.coef_, X.columns, columns=['Coefficient'])
coeff_df

Coefficient
VendorID                 -0.018587
passenger_count           0.016371
trip_distance             2.379258
RatecodeID                1.154826
PULocationID              0.000051
DOLocationID             -0.000482
payment_type              1.254765
extra                     0.012987
mta_tax                 -35.430841
tip_amount                0.566308
tolls_amount              0.111285
improvement_surcharge   -35.024193

In [16]:
y_pred = regressor.predict(X_test)

In [17]:
df2 = pd.DataFrame({'Actual': y_test, 'Predicted': y_pred})
df2

Actual  Predicted
308532     12.0  11.015227
628886      6.5   6.376962
1078005     4.5   5.960555
917321      6.0   7.273840
827820     12.0  10.459190
...         ...        ...
467268      7.5   8.353795
239326     21.0  19.083491
88066       6.0   7.100039
772260      7.0   6.700275
284233      3.5   5.672624

[249625 rows x 2 columns]

In [18]:
from sklearn.metrics import r2_score
r2_score(y_test,y_pred)

0.8787213412896456

# spark linear regression 

In [19]:
#df = pd.read_csv("yellow_tripdata_2019-01.csv")
#df = df.head(2000000)

In [20]:
spark_df = spark.createDataFrame(df)
spark_df.show(5)

+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+
|VendorID|passenger_count|trip_distance|RatecodeID|PULocationID|DOLocationID|payment_type|fare_amount|extra|mta_tax|tip_amount|tolls_amount|improvement_surcharge|total_amount|congestion_surcharge|
+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+
|       1|              1|          1.5|         1|         151|         239|           1|        7.0|  0.5|    0.5|      1.65|         0.0|                  0.3|        9.95|                 NaN|
|       1|              1|          2.6|         1|         239|         246|           1|       14.0|  0.5|    0.5|       1.0|         0.0|                  0.3|        16.3|                 NaN|
|       2|     

In [21]:
from pyspark.ml.feature import VectorAssembler

In [22]:
#choosing my features 
assembler = VectorAssembler(inputCols=['VendorID',
       'passenger_count', 'trip_distance', 'RatecodeID', 
       'PULocationID', 'DOLocationID', 'payment_type', 'extra',
       'mta_tax', 'tip_amount', 'tolls_amount', 'improvement_surcharge'],
                            outputCol='features')

In [23]:
df_out = assembler.transform(spark_df)
#df_out.show()

In [24]:
clean_df = df_out.select(['features', 'fare_amount'])
train_data,test_data=clean_df.randomSplit([0.7,0.3])
#train_data.describe().show()

In [25]:
from pyspark.ml.regression import LinearRegression
lr_model = LinearRegression(featuresCol='features',labelCol='fare_amount')
fit_model = lr_model.fit(train_data)

In [26]:
test_results = fit_model.evaluate(test_data)

In [27]:
#evaluating model
test_results.r2

0.882414380338879

# spark metrics

In [29]:
from pyspark.mllib.evaluation import RegressionMetrics
print("MSE = %s" % test_results.meanSquaredError)
print("RMSE = %s" % test_results.rootMeanSquaredError)
print("R-squared = %s" % test_results.r2)

MSE = 15.318449236930254
RMSE = 3.913879052414657
R-squared = 0.882414380338879


In [30]:
predictions = fit_model.transform(test_data)

In [31]:
#this is where the predictions will print
predictions.select("features",'fare_amount','prediction').show(5000)

+--------------------+-----------+------------------+
|            features|fare_amount|        prediction|
+--------------------+-----------+------------------+
|(12,[0,1,3,4,5,6]...|       18.0|34.559929028044465|
|(12,[0,1,3,4,5,6]...|       65.0|35.880538300607654|
|[1.0,0.0,0.0,1.0,...|        2.5| 6.259627612806142|
|[1.0,0.0,0.0,1.0,...|        2.5|  6.23814311702138|
|[1.0,0.0,0.0,1.0,...|        2.5| 4.961993675970177|
|[1.0,0.0,0.0,1.0,...|        2.5| 4.957415012934078|
|[1.0,0.0,0.0,1.0,...|        2.5| 6.177916087854236|
|[1.0,0.0,0.0,2.0,...|       52.0|12.783995108459049|
|[1.0,0.0,0.0,2.0,...|       52.0|  7.38177690791381|
|[1.0,0.0,0.0,2.0,...|       52.0| 8.926641565002264|
|[1.0,0.0,0.0,2.0,...|       52.0|10.497001758099788|
|[1.0,0.0,0.0,5.0,...|       60.0|27.190187537557684|
|[1.0,0.0,0.1,1.0,...|        2.5|6.4299551687978465|
|[1.0,0.0,0.2,1.0,...|        6.5|  4.18020759235057|
|[1.0,0.0,0.2,1.0,...|        3.0| 4.605287291040973|
|[1.0,0.0,0.2,1.0,...|      

In [32]:
#converting the predictions to pandas
predictions.select('fare_amount','prediction').toPandas()


fare_amount  prediction
0              18.0   34.559929
1              65.0   35.880538
2               2.5    6.259628
3               2.5    6.238143
4               2.5    4.961994
...             ...         ...
373436          5.0    6.402772
373437         11.5   11.550604
373438         42.5   63.502533
373439         52.0   52.056767
373440         20.5   20.222360

[373441 rows x 2 columns]

In [33]:
#converting predictions from pandas to text file

In [34]:
new_test_thing = predictions.select('fare_amount','prediction').toPandas()
new_test_thing

fare_amount  prediction
0              18.0   34.559929
1              65.0   35.880538
2               2.5    6.259628
3               2.5    6.238143
4               2.5    4.961994
...             ...         ...
373436          5.0    6.402772
373437         11.5   11.550604
373438         42.5   63.502533
373439         52.0   52.056767
373440         20.5   20.222360

[373441 rows x 2 columns]

In [35]:
new_test_thing.to_csv(index=False)

'fare_amount,prediction\n18.0,34.559929028044465\n65.0,35.880538300607654\n2.5,6.259627612806142\n2.5,6.23814311702138\n2.5,4.961993675970177\n2.5,4.957415012934078\n2.5,6.177916087854236\n52.0,12.783995108459049\n52.0,7.38177690791381\n52.0,8.926641565002264\n52.0,10.497001758099788\n60.0,27.190187537557684\n2.5,6.4299551687978465\n6.5,4.18020759235057\n3.0,4.605287291040973\n3.0,4.888453549440964\n3.0,5.401614797977981\n3.5,4.988337761974041\n3.5,5.6640874898119975\n4.0,5.651184892453969\n3.0,4.808945325628677\n3.5,4.736837685136905\n4.0,5.934915304751122\n4.0,5.400396341688861\n3.5,5.335233010469452\n3.5,5.323040846402833\n5.0,5.404349087302069\n4.5,5.272229362774766\n4.0,5.296707676290062\n4.5,5.40256626442099\n4.0,5.515740636642292\n5.0,5.511192880945238\n4.5,6.123999430439007\n4.0,6.09615568674489\n3.5,5.399893185584361\n3.5,6.172510434363467\n3.5,6.120163322841812\n4.0,6.120163322841812\n5.5,5.97751312962777\n4.0,5.430417212874147\n4.0,5.698684171961148\n4.5,5.413986771556999\n4

In [36]:
new_test_thing.to_csv('predictions_final.csv', sep='\t')

In [38]:
new_test_thing.to_csv(r'/Users/evanjoyce/Desktop/dataproject/prediction_final.csv')

# testing on data from covid month to see how model reacts

In [39]:
df_test_covid = pd.read_csv("yellow_tripdata_2020-02.csv")

/opt/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [40]:
df_test_covid = df_test_covid.head(1000000)

In [41]:
len(df_test_covid)

1000000

In [42]:
df_test_covid = df_test_covid.drop(['tpep_pickup_datetime'], axis=1)
df_test_covid = df_test_covid.drop(['tpep_dropoff_datetime'], axis=1)
df_test_covid = df_test_covid.drop(['store_and_fwd_flag'], axis=1)

In [43]:
df_test_covid = df_test_covid[df_test_covid['total_amount']>0]
df_test_covid = df_test_covid[df_test_covid['fare_amount']>0]
df_test_covid = df_test_covid[df_test_covid['total_amount']<300]
df_test_covid = df_test_covid[df_test_covid['fare_amount']<200]

In [44]:
len(df_test_covid)

996376

In [45]:
spark_df_test_covid = spark.createDataFrame(df_test_covid)
#spark_df_test_covid.show(5)

In [46]:
df_out_covid_test = assembler.transform(spark_df_test_covid)
#df_out_covid_test.show()

In [47]:
clean_df_covid = df_out_covid_test.select(['features', 'fare_amount'])

In [48]:
test_results_covid = fit_model.evaluate(clean_df_covid)

In [49]:
#training pre covid and testing during covid
test_results_covid.r2

0.8397283534974264

In [50]:
from pyspark.mllib.evaluation import RegressionMetrics
print("MSE = %s" % test_results_covid.meanSquaredError)
print("RMSE = %s" % test_results_covid.rootMeanSquaredError)
print("R-squared = %s" % test_results_covid.r2)

MSE = 18.825386131772845
RMSE = 4.338823127505067
R-squared = 0.8397283534974264


In [58]:
predictions2 = fit_model.transform(clean_df_covid)
#this is where the predictions will print
#predictions2.select("features",'fare_amount','prediction').show(5)
#converting the predictions to pandas
#predictions2.select('fare_amount','prediction').toPandas()
new_2 = predictions2.select('fare_amount','prediction').toPandas()
#new_2
#new_2.to_csv(index=False)


In [60]:
new_2.to_csv('secondary_tests_covid_month.csv', sep='\t')
new_2.to_csv(r'/Users/evanjoyce/Desktop/dataproject/extra_test_covid_month.csv')

# green taxi comparison

In [61]:
green_df = pd.read_csv("green_tripdata_2019-01 (1).csv")
green_df.head()

VendorID lpep_pickup_datetime lpep_dropoff_datetime store_and_fwd_flag  \
0         2  2018-12-21 15:17:29   2018-12-21 15:18:57                  N   
1         2  2019-01-01 00:10:16   2019-01-01 00:16:32                  N   
2         2  2019-01-01 00:27:11   2019-01-01 00:31:38                  N   
3         2  2019-01-01 00:46:20   2019-01-01 01:04:54                  N   
4         2  2019-01-01 00:19:06   2019-01-01 00:39:43                  N   

   RatecodeID  PULocationID  DOLocationID  passenger_count  trip_distance  \
0           1           264           264                5           0.00   
1           1            97            49                2           0.86   
2           1            49           189                2           0.66   
3           1           189            17                2           2.68   
4           1            82           258                1           4.53   

   fare_amount  extra  mta_tax  tip_amount  tolls_amount  ehail_fee  \
0          3.0    0.5      0.5        0.00           0.0        NaN   
1          6.0    0.5      0.5        0.00           0.0        NaN   
2          4.5    0.5      0.5        0.00           0.0        NaN   
3         13.5    0.5      0.5        2.96           0.0        NaN   
4         18.0    0.5      0.5        0.00           0.0        NaN   

   improvement_surcharge  total_amount  payment_type  trip_type  \
0                    0.3          4.30             2          1   
1                    0.3          7.30             2          1   
2                    0.3          5.80             1          1   
3                    0.3         19.71             1          1   
4                    0.3         19.30             2          1   

   congestion_surcharge  
0                   NaN  
1                   NaN  
2                   NaN  
3                   NaN  
4                   NaN

In [62]:
green_df.columns

Index(['VendorID', 'lpep_pickup_datetime', 'lpep_dropoff_datetime',
       'store_and_fwd_flag', 'RatecodeID', 'PULocationID', 'DOLocationID',
       'passenger_count', 'trip_distance', 'fare_amount', 'extra', 'mta_tax',
       'tip_amount', 'tolls_amount', 'ehail_fee', 'improvement_surcharge',
       'total_amount', 'payment_type', 'trip_type', 'congestion_surcharge'],
      dtype='object')

In [63]:
# X = df[['VendorID',
#        'passenger_count', 'trip_distance', 'RatecodeID', 
#        'PULocationID', 'DOLocationID', 'payment_type', 'extra',
#        'mta_tax', 'tip_amount', 'tolls_amount', 'improvement_surcharge']]
# y = df['fare_amount']

In [64]:
green_df = green_df.drop(['lpep_pickup_datetime'], axis=1)
green_df = green_df.drop(['lpep_dropoff_datetime'], axis=1)
green_df = green_df.drop(['store_and_fwd_flag'], axis=1)

In [65]:
green_df = green_df.drop(['ehail_fee'], axis=1)
#green_df = green_df.drop(['total_amount'], axis=1)
#green_df = green_df.drop(['payment_type'], axis=1)
green_df = green_df.drop(['trip_type'], axis=1)
#green_df = green_df.drop(['congestion_surcharge'], axis=1)

In [66]:
green_df = green_df [green_df ['total_amount']>0]
green_df= green_df [green_df ['fare_amount']>0]
green_df = green_df [green_df ['total_amount']<300]
green_df  = green_df [green_df ['fare_amount']<200]

In [67]:
green_df.columns

Index(['VendorID', 'RatecodeID', 'PULocationID', 'DOLocationID',
       'passenger_count', 'trip_distance', 'fare_amount', 'extra', 'mta_tax',
       'tip_amount', 'tolls_amount', 'improvement_surcharge', 'total_amount',
       'payment_type', 'congestion_surcharge'],
      dtype='object')

In [68]:
#new_green = green_df[['VendorID','passenger_count', 'trip_distance', 'RatecodeID', 'PULocationID', 'DOLocationID', 'payment_type', 'extra', 'mta_tax', 'tip_amount', 'tolls_amount', 'improvement_surcharge']].copy()

In [69]:
new_green= green_df[['VendorID', 'passenger_count', 'trip_distance', 'RatecodeID',
       'PULocationID', 'DOLocationID', 'payment_type', 'fare_amount', 'extra',
       'mta_tax', 'tip_amount', 'tolls_amount', 'improvement_surcharge',
       'total_amount', 'congestion_surcharge']]

In [70]:
#new_green.head()

In [71]:
new_green = new_green.head(1000000)

In [72]:
spark_green = spark.createDataFrame(new_green)
spark_green.show(5)

+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+
|VendorID|passenger_count|trip_distance|RatecodeID|PULocationID|DOLocationID|payment_type|fare_amount|extra|mta_tax|tip_amount|tolls_amount|improvement_surcharge|total_amount|congestion_surcharge|
+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+
|       2|              5|          0.0|         1|         264|         264|           2|        3.0|  0.5|    0.5|       0.0|         0.0|                  0.3|         4.3|                 NaN|
|       2|              2|         0.86|         1|          97|          49|           2|        6.0|  0.5|    0.5|       0.0|         0.0|                  0.3|         7.3|                 NaN|
|       2|     

In [73]:
df_out_green = assembler.transform(spark_green)
df_out_green.show(5)

+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+--------------------+
|VendorID|passenger_count|trip_distance|RatecodeID|PULocationID|DOLocationID|payment_type|fare_amount|extra|mta_tax|tip_amount|tolls_amount|improvement_surcharge|total_amount|congestion_surcharge|            features|
+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+--------------------+
|       2|              5|          0.0|         1|         264|         264|           2|        3.0|  0.5|    0.5|       0.0|         0.0|                  0.3|         4.3|                 NaN|[2.0,5.0,0.0,1.0,...|
|       2|              2|         0.86|         1|          97|          49|           2|        6.0|  0.5|    0.5|       0.0| 

In [74]:
green_clean = df_out_green.select(['features', 'fare_amount'])

In [75]:
test_green_clean = fit_model.evaluate(green_clean)

In [76]:
test_green_clean.r2

0.7771288701712671

In [77]:
from pyspark.mllib.evaluation import RegressionMetrics
print("MSE = %s" % test_green_clean.meanSquaredError)
print("RMSE = %s" % test_green_clean.rootMeanSquaredError)
print("R-squared = %s" % test_green_clean.r2)

MSE = 31.216992485415357
RMSE = 5.587216881902416
R-squared = 0.7771288701712671


In [78]:
predictions3 = fit_model.transform(green_clean)
#this is where the predictions will print
#predictions2.select("features",'fare_amount','prediction').show(5)
#converting the predictions to pandas
#predictions2.select('fare_amount','prediction').toPandas()
new_3 = predictions2.select('fare_amount','prediction').toPandas()
#new_2
#new_2.to_csv(index=False)

In [79]:
new_3.to_csv('secondary_tests_covid_month.csv', sep='\t')
new_3.to_csv(r'/Users/evanjoyce/Desktop/dataproject/extra_test_green_taxi.csv')

# Testing on different month 


In [81]:
# february 


In [82]:
feb_df = pd.read_csv("yellow_tripdata_2019-02.csv")
feb_df.head()

VendorID tpep_pickup_datetime tpep_dropoff_datetime  passenger_count  \
0         1  2019-02-01 00:59:04   2019-02-01 01:07:27                1   
1         1  2019-02-01 00:33:09   2019-02-01 01:03:58                1   
2         1  2019-02-01 00:09:03   2019-02-01 00:09:16                1   
3         1  2019-02-01 00:45:38   2019-02-01 00:51:10                1   
4         1  2019-02-01 00:25:30   2019-02-01 00:28:14                1   

   trip_distance  RatecodeID store_and_fwd_flag  PULocationID  DOLocationID  \
0            2.1           1                  N            48           234   
1            9.8           1                  N           230            93   
2            0.0           1                  N           145           145   
3            0.8           1                  N            95            95   
4            0.8           1                  N           140           263   

   payment_type  fare_amount  extra  mta_tax  tip_amount  tolls_amount  \
0             1          9.0    0.5      0.5         2.0           0.0   
1             2         32.0    0.5      0.5         0.0           0.0   
2             2          2.5    0.5      0.5         0.0           0.0   
3             2          5.5    0.5      0.5         0.0           0.0   
4             2          5.0    0.5      0.5         0.0           0.0   

   improvement_surcharge  total_amount  congestion_surcharge  
0                    0.3          12.3                   0.0  
1                    0.3          33.3                   0.0  
2                    0.3           3.8                   0.0  
3                    0.3           6.8                   0.0  
4                    0.3           6.3                   0.0

In [83]:
df_feb_test = feb_df.head(1250000)

In [84]:
len(df_feb_test)

1250000

In [85]:
df_feb_test = df_feb_test.drop(['tpep_pickup_datetime'], axis=1)
df_feb_test = df_feb_test.drop(['tpep_dropoff_datetime'], axis=1)
df_feb_test= df_feb_test.drop(['store_and_fwd_flag'], axis=1)

In [86]:
df_feb_test = df_feb_test[df_feb_test['total_amount']>0]
df_feb_test = df_feb_test[df_feb_test['fare_amount']>0]
df_feb_test = df_feb_test[df_feb_test['total_amount']<300]
df_feb_test = df_feb_test[df_feb_test['fare_amount']<200]

In [87]:
spark_df_feb_test = spark.createDataFrame(df_feb_test)
spark_df_feb_test.show(5)

+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+
|VendorID|passenger_count|trip_distance|RatecodeID|PULocationID|DOLocationID|payment_type|fare_amount|extra|mta_tax|tip_amount|tolls_amount|improvement_surcharge|total_amount|congestion_surcharge|
+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+
|       1|              1|          2.1|         1|          48|         234|           1|        9.0|  0.5|    0.5|       2.0|         0.0|                  0.3|        12.3|                 0.0|
|       1|              1|          9.8|         1|         230|          93|           2|       32.0|  0.5|    0.5|       0.0|         0.0|                  0.3|        33.3|                 0.0|
|       1|     

In [88]:
df_out_feb_test = assembler.transform(spark_df_feb_test)
df_out_feb_test.show(5)

+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+--------------------+
|VendorID|passenger_count|trip_distance|RatecodeID|PULocationID|DOLocationID|payment_type|fare_amount|extra|mta_tax|tip_amount|tolls_amount|improvement_surcharge|total_amount|congestion_surcharge|            features|
+--------+---------------+-------------+----------+------------+------------+------------+-----------+-----+-------+----------+------------+---------------------+------------+--------------------+--------------------+
|       1|              1|          2.1|         1|          48|         234|           1|        9.0|  0.5|    0.5|       2.0|         0.0|                  0.3|        12.3|                 0.0|[1.0,1.0,2.1,1.0,...|
|       1|              1|          9.8|         1|         230|          93|           2|       32.0|  0.5|    0.5|       0.0| 

In [89]:
clean_df_feb = df_out_feb_test.select(['features', 'fare_amount'])

In [90]:
test_results_feb = fit_model.evaluate(clean_df_feb)

In [91]:
test_results_feb.r2

0.8575080333311592

# spark metrics for feb 

In [92]:
from pyspark.mllib.evaluation import RegressionMetrics
print("MSE = %s" % test_results_feb.meanSquaredError)
print("RMSE = %s" % test_results_feb.rootMeanSquaredError)
print("R-squared = %s" % test_results_feb.r2)

MSE = 16.483044793384465
RMSE = 4.059931624225273
R-squared = 0.8575080333311592


In [93]:
predictions4= fit_model.transform(clean_df_feb)
#this is where the predictions will print
#predictions2.select("features",'fare_amount','prediction').show(5)
#converting the predictions to pandas
#predictions2.select('fare_amount','prediction').toPandas()
new_4 = predictions2.select('fare_amount','prediction').toPandas()
#new_2
#new_2.to_csv(index=False)

In [94]:
new_4.to_csv('secondary_tests_feb.csv', sep='\t')
new_4.to_csv(r'/Users/evanjoyce/Desktop/dataproject/extra_test_feb.csv')